In [4]:
# @version : 05/2023
# @author : grafika_jati
# 2D spherical LiDAR pixelization

# get 2D pixel image using 2D spherical approach
# X, Y and Z coordinate are normalized based on data train
# Training data is data taken from experiment #1,#2,#3,#4
# Testing Data is data taken from experiment #5
# Each pixel in 2D image has three channel X, R, A
# value in those channel also normalized based on Depth, Reflectivity, and Ambient (D,R,A) value over all contaminant and experiment in train data 


# Split train and test from dataset taken by # B. Schlager, T. Goelles, S. Muckenhuber and D. Watzenig, "Contaminations on Lidar Sensor Covers: Performance Degradation Including Fault Detection and Modeling as Potential Applications," in IEEE Open Journal of Intelligent Transportation Systems, vol. 3, pp. 738-747, 2022, doi: 10.1109/OJITS.2022.3214094.

import os
os.environ["CUDA_VISIBLE_DEVICES"] = "cuda:3"

from pathlib import Path
import os
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

# import pointcloudset as pcs
import pointcloudset.dataset as pcs #problem running all gpu
import torch

# if torch.cuda.is_available():
#   dev = "cuda:3"
#   print("yey")
# device = torch.device(dev)

print("Create 2D pixel image of 3D Lidar Data")

Read data for CNN


In [5]:
def lidar_to_2d_front_view(points, x_min_pos, y_min_pos, z_min_pos, x_max_pos, y_max_pos, z_max_pos, a_min, r_min, a_range, r_range, h_res_rad,v_res_rad,x_min_rad, x_max_rad, y_min_rad, y_max_rad, size_x, size_y, num_channel):
    
    x_lidar = points[:, 0] # in meters
    y_lidar = points[:, 1] # in meters
    z_lidar = points[:, 2] # in meters

    #get data 
    r_lidar = points[:, 3] # reflectivity
    a_lidar = points[:, 4] # ambient


    # print("COORDINATE")
    # print("x_lidar")
    # print(len(x_lidar))
    # print(x_lidar)

    # print("y_lidar")
    # print(len(y_lidar))
    # print(y_lidar)
    
    # print("i_lidar")
    # print(len(i_lidar))
    # print(i_lidar)


    # Distance relative to origin when looked from top
    # d_lidar = np.sqrt(x_lidar ** 2 + y_lidar ** 2) # clear
    # Absolute distance relative to origin
    d_lidar = np.sqrt(x_lidar ** 2 + y_lidar ** 2, z_lidar ** 2) # 

    #Normalisasi distance
    x_lidar_norm = (x_lidar-x_min_pos)/(x_max_pos-x_min_pos)
    y_lidar_norm = (y_lidar-y_min_pos)/(y_max_pos-y_min_pos)
    z_lidar_norm = (z_lidar-z_min_pos)/(z_max_pos-z_min_pos)
    d_lidar_norm = np.sqrt(x_lidar_norm ** 2 + y_lidar_norm ** 2 + z_lidar_norm ** 2) #


    # PROJECT INTO IMAGE COORDINATES
    # x_img = np.arctan2(-y_lidar, x_lidar)/ h_res_rad # minus to shift point to left
    x_img = np.arctan2(y_lidar, x_lidar)/ h_res_rad 
    y_img = np.arctan2(z_lidar, d_lidar)/ v_res_rad

    # print("PROJECTION")
    # print("x_img")
    # print(x_img)
    # print("y_img")
    # print(y_img)


    # SHIFT COORDINATES TO MAKE 0,0 THE MINIMUM
    
    #OS1-64 param lidar cover contamination
    x_img -= x_min_rad              # Shift

    # print("x_min")
    # print(x_min_rad)
    
    # print("x_max")
    # print(x_max_rad)

    y_img -= y_min_rad              # Shift 
  
    # print("Round")
    x_img=np.round(x_img)
    y_img=np.round(y_img)

    # print("x_img")
    # print(x_img)

    # print("y_img")
    # print(y_img)


    #check if there are same coordinate
     # get mean value for poin in same cluster or same coordinate
    arr_check = np.zeros([len(y_img),2]) # array to check if a point that have same coordinate position with other points, If some point projected in same coordinate, then we calculate mean value of feature from each point in the same cluster (coordinate)
    #assign each new coordinate from each point
    for kk in range(len(y_img)):
        arr_check[kk][0]=x_img[kk]
        arr_check[kk][1]=y_img[kk]

    uniqueRows = np.unique(arr_check, axis=0) # check unique coordinate

    # print("Unique coordinate")
    # print(len(uniqueRows))

    list_cluster=[[] for i in range(len(uniqueRows))] # list to save cluster of same coordinate
    for ii in range(len(uniqueRows)):
        nn=0
        for jj in range(len(arr_check)):
            if (uniqueRows[ii]==arr_check[jj]).all():
            # print(j)
                list_cluster[ii].append(jj) # put average value to this pixel coordinate
                nn=nn+1
        
    d_lidar_cluster=d_lidar_norm.copy()
    # i_lidar_cluster=i_lidar.copy()
    r_lidar_cluster=r_lidar.copy() 
    a_lidar_cluster=a_lidar.copy()



    #check mean if same coordinate
    #assign mean as new value
    for i in range(len(list_cluster)):
        d_temp_mean=0
        # i_temp_mean=0
        r_temp_mean=0
        a_temp_mean=0
        
        for j in range(len(list_cluster[i])):
            d_temp_mean += d_lidar_norm[list_cluster[i][j]]
            # i_temp_mean += i_lidar[list_cluster[i][j]]
            r_temp_mean += r_lidar[list_cluster[i][j]]
            a_temp_mean += a_lidar[list_cluster[i][j]]
                
        d_temp_mean=d_temp_mean/len(list_cluster[i])
        # i_temp_mean=i_temp_mean/len(list_cluster[i])
        r_temp_mean=r_temp_mean/len(list_cluster[i])
        a_temp_mean=a_temp_mean/len(list_cluster[i])

      
        # print(temp_mean)
        for j in range(len(list_cluster[i])):
            d_lidar_cluster[list_cluster[i][j]]=d_temp_mean
            # i_lidar_cluster[list_cluster[i][j]]=i_temp_mean
            r_lidar_cluster[list_cluster[i][j]]=r_temp_mean
            a_lidar_cluster[list_cluster[i][j]]=a_temp_mean

            
    
    # TODO create 2d array with x and y and pixel value 
    arr_single_img = np.zeros([num_channel, int(size_y), int(size_x)]) #  channel, row, coloumn 


    for k in range(len(r_lidar_cluster)): # Outer loop
        arr_single_img[0][int(y_img[k])][int(x_img[k])]= d_lidar_cluster[k] 
        # arr_single_img[0][int(y_img[k])][int(x_img[k])]=i_lidar_cluster[k]
        arr_single_img[1][int(y_img[k])][int(x_img[k])]= (r_lidar_cluster[k] - r_min) / r_range
        arr_single_img[2][int(y_img[k])][int(x_img[k])]= (a_lidar_cluster[k] - a_min) / a_range


    return arr_single_img

In [6]:
rootdir = "../Dataset/ouster_OS1-64_point_clouds_filter_data" # filter means only experiment that has point clouds 

print("tes read lidar data All- each points per experiment")


# constant parameter to normalized coordinate and attribute
# That value is taken from Dataset exp 1,2,3,4 over all type of contamiant 
# do normalization for testing dataset (exp 5) using value from training dataset
x_min_pos = 8.136452 # minimum coordinate point in x-axis
y_min_pos = -0.313579 # minimum coordinate point in y-axis
z_min_pos = -0.260452 # minimum coordinate point in z-axis

x_max_pos = 8.992307  # maximum coordinate point in x-axis
y_max_pos = 0.499952  # maximum coordinate point in y-axis
z_max_pos = 0.145646 # maximum coordinate point in z-axis


a_min = 0.0 # minimun value of ambient
r_min = 59.0 # minimun value of reflectivity

a_max = 472.0 # maximum value of ambient
r_max = 19528.0 # maximum value of reflectivity

a_range = a_max-a_min # minimun value of ambient
r_range = r_max-r_min # range value of reflectivity

#Lidar OS1-64 Spec
# h_res = 0.1 # 70         # horizontal resolution (assuming 20Hz setting), the smaller, the bigger the 2D projection image
# v_res = 0.1 # 30          # vertical res

h_res = 0.5 # 16         # horizontal resolution (assuming 20Hz setting), the smaller, the bigger the 2D projection image
v_res = 0.5 # 9          # vertical res


# D,R,A
num_channel = 3 # number of channel


# Convert to Radians
h_res_rad = h_res * (np.pi/180)# radians
v_res_rad = v_res * (np.pi/180) # radians

x_min_rad=np.round(np.arctan2(y_min_pos, x_min_pos)/h_res_rad)
x_max_rad=np.round(np.arctan2(y_max_pos, x_max_pos)/h_res_rad)

d_lidar_min_rad = np.sqrt(x_min_pos ** 2 + y_min_pos ** 2 + z_min_pos ** 2) 
d_lidar_max_rad = np.sqrt(x_max_pos ** 2 + y_max_pos ** 2 + z_max_pos ** 2) 

y_min_rad=np.round(np.arctan2(z_min_pos, d_lidar_min_rad)/v_res_rad)
y_max_rad=np.round(np.arctan2(z_max_pos, d_lidar_max_rad)/v_res_rad)

size_x = (x_max_rad-x_min_rad)+3
size_y = (y_max_rad-y_min_rad)+3



		
# each dir create an array
df_temp = pd.DataFrame()
df_temp = pd.DataFrame(columns = ['class', 'exp', 'data'])

for dirs in os.listdir(rootdir):
	n=0
	temp_dir=str(rootdir+"/"+dirs)
	# print(dirs)

	name = dirs.split('_')
	name_temp= name[2] # get name of contaminant

	contaminant_type=name_temp[:-1] # remove number of experiment
	exp=name_temp[-1]
	
	if contaminant_type=="reference-with-cove":
		contaminant_type="cover"
		exp=1
		
	elif contaminant_type=="reference-without-cove":
		contaminant_type="no_cover"
		exp=1

	elif contaminant_type=="artificial-dirt-05m":
		contaminant_type="dirt_05mm"
		exp=1

	elif contaminant_type=="artificial-dirt-10m":
		contaminant_type="dirt_10mm"
		exp=1

	elif contaminant_type=="artificial-dirt-15m":
		contaminant_type="dirt_15mm"
		exp=1


	for filename in os.listdir(temp_dir):
	# print("filename")
	# print(filename)

		if filename.endswith(".parquet"): #check if lidar data is exist
        
			ouster_data = pcs.Dataset.from_file(Path("../Dataset/ouster_OS1-64_point_clouds_filter_data/"+str(dirs)))
			df_points = ouster_data[n].data[["x","y","z", "reflectivity", "ambient"]]
			
			if not df_points.empty:
				# print('DataFrame is empty!')

				lidar= df_points.to_numpy()

			#get single image of lidar per contaminant and experiment
				single_img_lidar = lidar_to_2d_front_view(lidar, x_min_pos, y_min_pos, z_min_pos, x_max_pos, y_max_pos,z_max_pos, a_min, r_min, a_range, r_range, h_res_rad, v_res_rad, x_min_rad, x_max_rad, y_min_rad, y_max_rad, size_x, size_y, num_channel)
				df_temp = df_temp.append({'class' : contaminant_type, 'exp' : exp, 'data': single_img_lidar},ignore_index = True)
    
			n=n+1



df_temp.to_json('lidar_norm_train_test_2d_spherical_10class_norm_DRA_9x16.json')



tes read lidar data All- each points per experiment


/tmp/ipykernel_3801516/2215582763.py:121: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_temp = df_temp.append({'class' : contaminant_type, 'exp' : exp, 'data': single_img_lidar},ignore_index = True)
/tmp/ipykernel_3801516/2215582763.py:121: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_temp = df_temp.append({'class' : contaminant_type, 'exp' : exp, 'data': single_img_lidar},ignore_index = True)
/tmp/ipykernel_3801516/2215582763.py:121: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_temp = df_temp.append({'class' : contaminant_type, 'exp' : exp, 'data': single_img_lidar},ignore_index = True)
/tmp/ipykernel_3801516/2215582763.py:121: FutureWarning: The frame.append method is deprecated and will be removed from pandas 

In [7]:
# df = pd.read_json('lidar_norm_train_test_2d_spherical_10class_DRA_9x16.json')
df = pd.read_json('lidar_norm_train_test_2d_spherical_10class_norm_DRA_9x16.json')


In [8]:
df

class  exp                                               data
0            oil    1  [[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...
1            oil    1  [[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...
2            oil    1  [[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...
3            oil    1  [[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...
4            oil    1  [[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...
...          ...  ...                                                ...
10602  dirt_05mm    1  [[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...
10603  dirt_05mm    1  [[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...
10604  dirt_05mm    1  [[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...
10605  dirt_05mm    1  [[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...
10606  dirt_05mm    1  [[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...

[10607 rows x 3 columns]

In [12]:
df.iloc[0][2]

[[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0,
   0.0,
   0.6116245389,
   0.6051670909,
   0.638700068,
   0.6877154112,
   0.7528414726,
   0.8374392986,
   0.8920071721,
   0.0,
   0.0,
   0.0,
   0.0],
  [0.0,
   0.0,
   0.601824522,
   0.6337357759000001,
   0.6837655306,
   0.7363225222,
   0.8029388189000001,
   0.8789805770000001,
   0.9266662598000001,
   0.0,
   0.0,
   0.0,
   0.0],
  [0.0,
   0.0,
   0.6690874696,
   0.7272319198,
   0.7756639719,
   0.8324499726,
   0.8799337149,
   0.9326297045,
   0.9850913882000001,
   0.0,
   0.0,
   0.0,
   0.0],
  [0.0,
   0.0,
   0.8463585973000001,
   0.8640682697000001,
   0.9004963636000001,
   0.9341911077,
   0.9756556153,
   1.0322490931,
   1.0802395344,
   0.0,
   0.0,
   0.0,
   0.0],
  [0.0,
   0.0,
   0.9724364281000001,
   0.9843378067,
   1.0045435429,
   1.0390762091,
   1.0859547853,
   1.1379076242,
   1.1730314493,
   0.0,
   0.0,
   0.0,
   0.0],
  [0.0,
   0.0,
   1.1394346952,
   1.1